In [ ]:
!pip install -q openai wordfreq

73132.92s - pydevd: Sending message related to process being replaced timed-out after 5 seconds


You should consider upgrading via the '/Users/michaelryaboy/recent-projects/inference-webhook/venv/bin/python3 -m pip install --upgrade pip' command.


In [ ]:
# 🟢 Cell 2 – imports & client
import os
from typing import List, Literal
from openai import OpenAI
from pydantic import BaseModel, Field

client = OpenAI(
    base_url="https://api.inference.net/v1",          # inference.net endpoint
    api_key=os.getenv("INFERENCE_API_KEY"),
)
MODEL = "google/gemma-3-27b-instruct/bf-16"

In [ ]:
import requests

response = requests.get("https://gist.githubusercontent.com/mrmps/fbf29299d4b4401e6cfd659fd637fe41/raw/10920268c7a806778b954568f88a1734ea59ca8a/gistfile1.txt")

raw_domains = response.text.split("\n")

In [179]:
import re
from wordfreq import zipf_frequency   # pip install wordfreq

VOWELS = set("aeiou")

def looks_good(domain: str) -> bool:
    """
    Heuristically decide whether `domain` is worth a closer look.

    • Accepts **any** TLD (only rejects punycode or multi‑dot domains)
    • ASCII letters only in the SLD  (no digits, hyphens, punycode)
    • 4–16 chars, at least one vowel *and* one consonant
    • Balanced vowel ratio: 0.2 – 0.8
    • No 4‑char runs of vowels or consonants, no triple repeats,
      no doubled first letter (“aafoo”), no placeholder words
    • Must look *somewhat* like an English word (Zipf ≥ 1.2) **or**
      contain an English sub‑chunk ≥ 4 letters with Zipf ≥ 3.0
    """

    domain = domain.strip().lower()

    if domain.startswith("xn--") or domain.count(".") != 1:
        return False

    sld, _, _ = domain.partition(".")
    if not 4 <= len(sld) <= 16:
        return False
    if not re.fullmatch(r"[a-z]+", sld):
        return False

    if sld[0] == sld[1]:
        return False
    if re.search(r"(.)\1\1", sld):
        return False
    if re.search(r"[aeiou]{4,}", sld) or re.search(r"[bcdfghjklmnpqrstvwxyz]{4,}", sld):
        return False
    if re.fullmatch(r"(?:[bcdfghjklmnpqrstvwxyz][aeiou]){4,}", sld):
        return False

    v = sum(c in VOWELS for c in sld)
    if v == 0 or v == len(sld):
        return False
    ratio = v / len(sld)
    if not (0.20 <= ratio <= 0.80):
        return False

    freq = zipf_frequency(sld, "en")
    if freq >= 1.2:
        return True

    for i in range(len(sld) - 3):
        chunk = sld[i:i+4]
        if zipf_frequency(chunk, "en") >= 3.0:
            return True

    return False

domains = [d for d in raw_domains if looks_good(d)]
print("Len Filtered list →", len(domains))
print("first 10 domains →", domains[:10])
# show number of domains by tld and top domains by tld
tld_counts = {}
for domain in domains:
    tld = domain.split(".")[-1]
    tld_counts[tld] = tld_counts.get(tld, 0) + 1

print(tld_counts)

# show top domains by tld

Len Filtered list → 52002
first 10 domains → ['ababanews.net', 'ababeelrealtors.com', 'abacombs.com', 'abacotoner.com', 'abadcult.org', 'abannebebek.com', 'abanoteolo.it', 'abarcart.com', 'abarrotesbombin.click', 'abaseballtime.com']
{'net': 2102, 'com': 29676, 'org': 1447, 'it': 144, 'click': 225, 'online': 1717, 'store': 1059, 'xyz': 841, 'site': 1416, 'top': 1613, 'su': 21, 'biz': 235, 'sk': 21, 'shop': 1902, 'one': 86, 'love': 33, 'pro': 145, 'blog': 121, 'tech': 221, 'in': 134, 'website': 189, 'beauty': 12, 'ru': 709, 'giving': 3, 'uk': 142, 'space': 422, 'agency': 44, 'properties': 5, 'co': 132, 'mobi': 50, 'wiki': 37, 'wtf': 21, 'info': 835, 'technology': 7, 'cab': 4, 'app': 257, 'cloud': 132, 'dev': 112, 'global': 14, 'solutions': 37, 'paris': 4, 'trade': 11, 'cc': 68, 'clothing': 8, 'ltd': 31, 'ro': 38, 'fun': 189, 'skin': 11, 'life': 175, 'digital': 84, 'today': 89, 'se': 234, 'capital': 12, 'ca': 67, 'live': 248, 'art': 96, 'finance': 21, 'best': 20, 'fr': 60, 'world': 100, 

In [180]:
import json
from pydantic import BaseModel, Field, ConfigDict


# 🟢 Cell 3 – Pydantic schema (reasoning BEFORE score)
class DomainValuation(BaseModel):
    reasoning: str
    score:  str

    model_config = ConfigDict(extra='forbid')   


SYSTEM_PROMPT = """
Senior domain appraiser (15yr experience). Estimate open market value based on expertise and historical sales. Focus on resale value, strengths/weaknesses, realistic price ranges.

Valuation factors:
1. Extension (.com best, .net/.org good, .io/.ai tech, others situational)
2. Length (<8 excellent, 9-12 good, 13-15 ok, 16+ bad)
3. Words (dictionary > brandable > acronym > random)
4. Pronounceability (radio test: spell after hearing once?)
5. Brandability (unique/intuitive, no hyphens/numbers unless industry-specific)
6. Search volume (existing searches = demand)
7. Commercial viability (B2B > B2C > hobby; revenue potential)
8. Industry (AI/crypto/finance/health/SaaS = premium)
9. Development potential (real business vs parking)
10. Trademark risk (generic > distinctive)
11. Comparable sales (actual sales, not asking prices)
12. Market timing (emerging vs saturated sectors)
13. Language (global appeal? cultural issues?)
14. Liquidity (how fast to flip? who buys?)

Scoring/Values:
95-100: Legendary ($500K-$10M+) - AI.com level
90-94: Elite ($100K-$500K) - Single-word .com hot sectors
80-89: Premium ($25K-$100K) - Quality two-word .com
70-79: Valuable ($5K-$25K) - Good brandables, strong keywords
60-69: Marketable ($1K-$5K) - Decent brands, niche terms
50-59: Speculative ($500-$1K) - Trending keywords, needs development
40-49: Marginal ($100-$500) - Long/meaningful, weak extensions
30-39: Minimal ($50-$100) - Specific end-user only
20-29: Weak ($10-$50) - Poor brand, length issues
10-19: Junk (reg fee) - Random strings, no market
1-9: Toxic (abandon) - Trademark violations, offensive

Key questions:
- Would YOU invest at this price?
- Name 3 potential buyers and why?
- Pass radio/billboard test?
- Similar domains sold?
- Would business build on this vs better alternative?

Output JSON: reasoning → score
'reasoning' = concise but thorough explanation with key factors, buyer scenarios, price justification.

Reality: 90% of domains worth < renewal fee. Be ruthlessly honest. Good domain = "I'd buy that myself."
""".strip()

In [181]:
DOMAIN_SCHEMA = {
    "name":   "domain_valuation",
    "strict": True,
    "schema": DomainValuation.model_json_schema()      # auto‑generated 🎉
}

print(DOMAIN_SCHEMA)

{'name': 'domain_valuation', 'strict': True, 'schema': {'additionalProperties': False, 'properties': {'reasoning': {'title': 'Reasoning', 'type': 'string'}, 'score': {'title': 'Score', 'type': 'string'}}, 'required': ['reasoning', 'score'], 'title': 'DomainValuation', 'type': 'object'}}


In [182]:
def make_line(domain: str):
    body = {
        "model": MODEL,
        "messages": [
            {"role": "system", "content": SYSTEM_PROMPT},
            {"role": "user",   "content": f"Domain: {domain}"}
        ],
        "response_format": {           # structured outputs!
            "type": "json_schema",
            "json_schema": DOMAIN_SCHEMA
        },
        "temperature": 0.3,
        "max_tokens": 1200
    }
    return {
        "custom_id": domain,
        "method": "POST",
        "url": "/v1/chat/completions",
        "body": body
    }

In [184]:
import json
MAX_LINES = 45000
items = domains[:MAX_LINES]  # use your actual list variable

# Write the file, one request per line using make_line
with open("batchinput.jsonl", "w", encoding="utf-8") as f:
    for i, dom in enumerate(items):
        line = make_line(dom.strip())
        f.write(f"{json.dumps(line)}\n")

# Upload the file using openai.files.create
batch_input_file = client.files.create(
    file=open("batchinput.jsonl", "rb"),
    purpose="batch"
)

print(batch_input_file)

FileObject(id='cknhPTD5lPj7aAxkMTKZE', bytes=None, created_at=1753907090636, filename=None, object=None, purpose=None, status=None, expires_at=None, status_details=None)


In [185]:
batch = client.batches.create(
    input_file_id=batch_input_file.id,
    endpoint="/v1/chat/completions",
    completion_window="24h",
    # Optional.
    metadata={
        "description": "domain classification"
    },
)

print(batch)

Batch(id='0E5A4ldfAEv7K8cPaVQ6s', completion_window='24h', created_at=1753907100704, endpoint='/v1/chat/completions', input_file_id='cknhPTD5lPj7aAxkMTKZE', object='batch', status='in_progress', cancelled_at=None, cancelling_at=None, completed_at=None, error_file_id=None, errors=None, expired_at=None, expires_at=1753993500703, failed_at=None, finalizing_at=None, in_progress_at=1753907100703, metadata={'description': 'domain classification'}, output_file_id=None, request_counts=BatchRequestCounts(completed=0, failed=0, total=45000))


In [194]:
print(batch.error_file_id)

None


In [187]:
import pandas as pd
import time

# Use helpers from llm-translation.ipynb
def wait_for_batch(client, batch_id: str, interval: int = 2):
    """Poll the batch until it completes; returns final status object."""
    while True:
        status = client.batches.retrieve(batch_id)
        if status.status == "completed":
            return status
        print("Status:", status.status)
        time.sleep(interval)

def ndjson_to_dicts(client, file_id: str):
    """Download a file and parse ND‑JSON into a list of dicts, skipping blanks."""
    text = client.files.content(file_id).text
    return [json.loads(line) for line in text.splitlines() if line.strip()]

# ── 1. Wait for the batch to finish ─────────────────────────────────────────────
status = wait_for_batch(client, batch.id)
output_records = ndjson_to_dicts(client, status.output_file_id)

df = pd.DataFrame(columns=["domain", "reasoning", "score"])
for line_obj in output_records:
    # The response structure is: {"response": {"body": {"choices": [{"message": {"content": ...}}]}}}
    message_content = (
        line_obj["response"]["body"]["choices"][0]["message"]["content"]
    )
    content_json = json.loads(message_content)
    reasoning = content_json.get("reasoning", "")
    score = content_json.get("score", "")
    domain = line_obj.get("custom_id", "")
    df.loc[len(df)] = [domain, reasoning, score]

df

JSONDecodeError: Expecting value: line 3 column 851 (char 2433)

In [196]:
result = client.batches.retrieve(batch.id)
error_file = client.files.content(result.error_file_id)
print(error_file.text)

{"id":"0E5A4ldfAEv7K8cPaVQ6s","custom_id":"thebossladytote.com","response":null,"error":{"code":"inference_failed","message":"Maximum retries reached"}}
{"id":"0E5A4ldfAEv7K8cPaVQ6s","custom_id":"thebookvoyager.com","response":null,"error":{"code":"inference_failed","message":"Maximum retries reached"}}
{"id":"0E5A4ldfAEv7K8cPaVQ6s","custom_id":"thebookstorebook.com","response":null,"error":{"code":"inference_failed","message":"Maximum retries reached"}}
{"id":"0E5A4ldfAEv7K8cPaVQ6s","custom_id":"thebookemart.com","response":null,"error":{"code":"inference_failed","message":"Maximum retries reached"}}
{"id":"0E5A4ldfAEv7K8cPaVQ6s","custom_id":"thebookhavengh.com","response":null,"error":{"code":"inference_failed","message":"Maximum retries reached"}}
{"id":"0E5A4ldfAEv7K8cPaVQ6s","custom_id":"thebookclub.top","response":null,"error":{"code":"inference_failed","message":"Maximum retries reached"}}
{"id":"0E5A4ldfAEv7K8cPaVQ6s","custom_id":"theboneyard.xyz","response":null,"error":{"code